In [10]:
from skewPy import SkewT
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import glob
from datetime import datetime

import seaborn as sns; sns.set()
sns.set_style("ticks")
sns.set_context("talk")
sns.set_style({'xtick.minor.size': '1.0'})

# Interpolates a single variable data_in from A SINGLE .TXT FILE onto goal_hghts
def interp_all(data_str, goal_hghts, data_in):
    data_out = np.empty([len(goal_hghts), data_in[data_str].shape[1]])
    for i in range(data_in[data_str].shape[1]):
        hght_mask = np.where(data_in['hght'][:,i].mask == False)
        data_mask = np.where(data_in[data_str][:,i].mask == False)
        data_out[:,i] = np.interp(goal_hghts, data_in['hght'][:,i][hght_mask], data_in[data_str][:,i][hght_mask])
        data_out[np.where(data_out == -999)] = np.nan
    return(data_out)

# Interpolates a data_set from full monthly data formed from many files 
def interp_all_monthly(data_set_in, goal_hghts, data_str):
    data_out = np.empty([len(goal_hghts), ntimes])
    idx_start = 0
    for i in range(len(data_set_in)):
        idx_end = idx_start + data_set_in[i]['hght'].shape[1]
        #print(data_out[:, idx_start:idx_end].shape)
        #print('goal hghts', goal_hghts)
        for j in range(idx_end - idx_start):
            hght_mask = np.where(data_set_in[i]['hght'][:,j].mask == False)
            data_mask = np.where(data_set_in[i][data_str][:,j].mask == False)
            #print('actual hghts', data_set_in[i]['hght'][:,j][hght_mask])
            #print('actual hghts shape', data_set_in[i]['hght'][:,j][hght_mask].shape)
            #print('hght_mask shape ', hght_mask[0].shape)
            #print('data_mask shape ', data_mask[0].shape)
            data_interp = data_set_in[i][data_str][:,j][hght_mask]
            data_interp[np.where(data_interp == -999)] = np.nan
            data_out[:, idx_start+j] = np.interp(goal_hghts, \
                                       data_set_in[i]['hght'][:,j][hght_mask], \
                                       data_set_in[i][data_str][:,j][hght_mask], left=np.nan, right=np.nan)
            #print(data_out[0, idx_start+j])
        idx_start = idx_end
    return(data_out)

# Function which takes a dictionary data_in and interpolate a key data_str onto heights
# goal_hghts. Might update to have automatically cycle through dictionary keys rather than
# take data_str, but not too many variables of interest to read
def interp_all_thompson(data_str, goal_hghts, data_in):
    data_out = np.empty([len(goal_hghts), len(data_in)])
    for i in range(len(data_in)):
        #print(data_in[i]['hght'])
        #print(data_in[i][data_str])
        data_out[:,i] = np.interp(goal_hghts, data_in[i]['hght'], data_in[i][data_str])
        #print(data_in[i]['hght'].max())
        #print(goal_hghts>data_in[i]['hght'].max())
        data_out[np.where(goal_hghts>data_in[i]['hght'].max()), i] = np.nan
    return(data_out)


In [11]:
# Plots the most recent sounding from each site
plt.close('all')

S1 = SkewT.Sounding(filename='/Volumes/cruiseshare/Soundings/Palau/91408_KororPalau/201808.txt', fmt='PALAU', date_to_read = -1, init_plot = 0)
S1.make_skewt_axes()
S1.add_profile(color='r', bloc=.6, bcol='r')
S1.readfile('/Volumes/cruiseshare/Soundings/Yap/201808.txt')
S1.add_profile(color='b', bloc=.8, bcol='b')

read_folder = '/Volumes/cruiseshare/Soundings/Thompson/edt/'
file_list = sorted(glob.glob(read_folder + '*'))
S1.readfile(file_list[-1], fmt='PISTON_EDT')
S1.add_profile(color='k', bloc=1, bcol='k', fmt='PISTON_EDT')



p_lcl =  948.88788458
lcl_height =  507.0


In [12]:
####################################
# Processes Palau for August 2018 #
####################################

file_list = list('/Volumes/cruiseshare/Soundings/Palau/91408_KororPalau/201808.txt')

palau = SkewT.Sounding(filename='/Volumes/cruiseshare/Soundings/Palau/91408_KororPalau/201808.txt', fmt='PALAU', date_to_read = 0, init_plot = 0)

# Reads Palau for August

ntimes = 0 #number of days
ntimes = ntimes + palau.data['temp'].shape[1]
print(ntimes)
#S1.fig.legend()

#temp = np.empty(palau['temp'].shape)
z = np.linspace(0, 17000, 300)
#for i in range(len(z)palau['hght'].shape[1]):
#    temp[:,i] = np.interp(z, palau['hght'][:,i], palau['temp'][:,i])
    #dwpt = interp_all(palau, z, 'dwpt')
    #pres = interp_all(palau, z, 'pres')

pal_temp = interp_all('temp', z, palau)
pal_dwpt = interp_all('dwpt', z, palau)
pal_sknt = interp_all('sknt', z, palau)
pal_drct = interp_all('drct', z, palau)
pal_dwpt[np.where((pal_dwpt > 50.) | (pal_dwpt < -100))] = np.nan


pal_relh = SkewT.RH(pal_temp, pal_dwpt)
pal_u = pal_sknt*np.cos(np.radians(270-pal_drct))
pal_v = pal_sknt*np.sin(np.radians(270-pal_drct))

# Some data management




111


/Users/zanemartin/anaconda/lib/python3.6/site-packages/ipykernel/__main__.py:27: RuntimeWarning: invalid value encountered in greater
/Users/zanemartin/anaconda/lib/python3.6/site-packages/ipykernel/__main__.py:27: RuntimeWarning: invalid value encountered in less


In [4]:
####################################
# Processes Yap for August 2018 #
####################################

file_list = list('/Volumes/cruiseshare/Soundings/Yap/201808.txt')

yap = SkewT.Sounding(filename='/Volumes/cruiseshare/Soundings/Yap/201808.txt', fmt='PALAU', date_to_read = 0, init_plot = 0)

# Reads Palau for August

ntimes = 0 #number of days
ntimes = ntimes + yap.data['temp'].shape[1]
print(ntimes)


yap_temp = interp_all('temp', z, yap)
yap_dwpt = interp_all('dwpt', z, yap)
yap_sknt = interp_all('sknt', z, yap)
yap_drct = interp_all('drct', z, yap)

# Some data management
yap_dwpt[np.where((yap_dwpt > 50.) | (yap_dwpt < -100))] = np.nan

yap_relh = SkewT.RH(yap_temp, yap_dwpt)
yap_u = yap_sknt*np.cos(np.radians(270-yap_drct))
yap_v = yap_sknt*np.sin(np.radians(270-yap_drct))


56


/Users/zanemartin/anaconda/lib/python3.6/site-packages/ipykernel/__main__.py:22: RuntimeWarning: invalid value encountered in greater
/Users/zanemartin/anaconda/lib/python3.6/site-packages/ipykernel/__main__.py:22: RuntimeWarning: invalid value encountered in less


In [5]:
####################################
# Processes Thompson for August 2018 #
####################################

# Main folder where the reading is done; creates list of all current soundings
read_folder = '/Volumes/cruiseshare/Soundings/Thompson/edt/'
file_list = sorted(glob.glob(read_folder + '*'))
#print('List of soundings: ', file_list)
#print('Most current sounding: ', file_list[-1])

# Read the most recent one
thompson = SkewT.Sounding(data={}, fmt='PISTON_EDT')
#thompson.make_skewt_axes()
thompson_data = ()
thompson_date_list = ()

clrs = sns.color_palette('colorblind', len(file_list))

for file_name,idx in zip(file_list, np.arange(len(file_list))):
    thompson.readfile(file_name)
    #S1.add_profile(color=clrs[-idx], bloc=.6 + .2*idx, bcol=clrs[-idx])
    thompson_data = np.append(thompson_data, thompson.data)
    thompson_date_list = np.append(thompson_date_list, thompson.sounding_date)

# Sets up goal heights up to 20km and interpolate tempa nd dewpt
#pres = np.linspace(100, 1000, 1000)
#temp = interp_all('temp', pres[::-1], data_set)
#dwpt = interp_all('dwpt', pres[::-1], data_set)
#pres = interp_all('pres', pres[::-1], data_set)

tom_temp = interp_all_thompson('temp', z, thompson_data)
tom_dwpt = interp_all_thompson('dwpt', z, thompson_data)
tom_pres = interp_all_thompson('pres', z, thompson_data)


# Calculates zonal and meridional wind from the speed and direction
tom_u = np.empty([len(z), len(thompson_data)])
tom_v = np.empty(tom_u.shape)

for i in range(len(thompson_data)):
    tom_utemp = thompson_data[i]['sknt']*np.cos(np.radians(270-thompson_data[i]['drct']))
    tom_vtemp = thompson_data[i]['sknt']*np.sin(np.radians(270-thompson_data[i]['drct']))
    tom_utemp = np.interp(z, thompson_data[i]['hght'], tom_utemp, left=np.nan, right=np.nan)
    tom_vtemp = np.interp(z, thompson_data[i]['hght'], tom_vtemp, left=np.nan, right=np.nan)
    tom_utemp[np.where(z>thompson_data[i]['hght'].max())] = np.nan
    tom_vtemp[np.where(z>thompson_data[i]['hght'].max())] = np.nan
    tom_u[:,i] = tom_utemp
    tom_v[:,i] = tom_vtemp
#print(u)

# Calculates relative humidity; might also read in and compare if in sounding
tom_relh = SkewT.RH(tom_temp, tom_dwpt)

In [7]:
fig = plt.figure()
ax1 = fig.add_subplot(3,1,1)
ax2 = fig.add_subplot(3,1,2)
ax3 = fig.add_subplot(3,1,3)

cf = ax1.contourf(palau.sounding_date[79:], z, pal_u[:, 79:], np.arange(-60, 60), cmap='RdBu_r', extend='both')
ax1.set_title('Palau Zonal wind (knots)')
ax1.set_xlim([datetime(2018, 8, 21, 0, 0),datetime(2018, 8, 28, 12, 0)])
plt.colorbar(cf, ax=ax1)

cf = ax2.contourf(yap.sounding_date[40:], z, yap_u[:, 40:], np.arange(-60, 60), cmap='RdBu_r', extend='both')
ax2.set_title('Yap Zonal wind (knots)')
ax2.set_xlim([datetime(2018, 8, 21, 0, 0),datetime(2018, 8, 28, 12, 0)])
plt.colorbar(cf, ax=ax2)

cf = ax3.contourf(thompson_date_list, z, tom_u, np.arange(-60, 60), cmap='RdBu_r', extend='both')
ax3.set_title('Thompson Zonal wind (knots)')
ax3.set_xlim([datetime(2018, 8, 21, 0, 0),datetime(2018, 8, 28, 12, 0)])
plt.colorbar(cf, ax=ax3)

fig.tight_layout()
plt.show()


In [8]:
fig = plt.figure()
ax1 = fig.add_subplot(3,1,1)
ax2 = fig.add_subplot(3,1,2)
ax3 = fig.add_subplot(3,1,3)

cf = ax1.contourf(palau.sounding_date[79:], z, pal_v[:,79:], np.arange(-30, 30), cmap='RdBu_r', extend='both')
ax1.set_title('Palau Meridional wind (knots)')
ax1.set_xlim([datetime(2018, 8, 21, 0, 0),datetime(2018, 8, 28, 12, 0)])
plt.colorbar(cf, ax=ax1)

cf = ax2.contourf(yap.sounding_date[40:], z, yap_v[:,40:], np.arange(-30, 30), cmap='RdBu_r', extend='both')
ax2.set_title('Yap Meridional wind (knots)')
ax2.set_xlim([datetime(2018, 8, 21, 0, 0),datetime(2018, 8, 28, 12, 0)])
plt.colorbar(cf, ax=ax2)

cf = ax3.contourf(thompson_date_list, z, tom_v, np.arange(-30, 30), cmap='RdBu_r', extend='both')
ax3.set_title('Thompson Meridional wind (knots)')
ax3.set_xlim([datetime(2018, 8, 21, 0, 0),datetime(2018, 8, 28, 12, 0)])
plt.colorbar(cf, ax=ax3)

fig.tight_layout()
plt.show()



In [9]:
def make_anom(data_in):
    data_out = np.empty(data_in.shape)
    for i in range(data_in.shape[1]):
        data_out[:,i] = data_in[:,i] - np.nanmean(data_in, 1)
    return(data_out)
                        
pal_relha = make_anom(pal_relh)
yap_relha = make_anom(yap_relh)
tom_relha = make_anom(tom_relh)

if 1 ==1:
    fig = plt.figure()
    ax1 = fig.add_subplot(3,1,1)
    ax2 = fig.add_subplot(3,1,2)
    ax3 = fig.add_subplot(3,1,3)

    cf = ax1.contourf(palau.sounding_date[79:], z, pal_relha[:,79:], cmap='RdBu_r', extend='both')
    ax1.set_title('Palau Relative Humidity Anomaly (%)')
    ax1.set_xlim([datetime(2018, 8, 21, 0, 0),datetime(2018, 8, 28, 12, 0)])
    plt.colorbar(cf, ax=ax1)

    cf = ax2.contourf(yap.sounding_date[40:], z, yap_relha[:,40:], cmap='RdBu_r', extend='both')
    ax2.set_title('Yap Relative Humidity Anomaly (%)')
    ax2.set_xlim([datetime(2018, 8, 21, 0, 0),datetime(2018, 8, 28, 12, 0)])
    plt.colorbar(cf, ax=ax2)

    cf = ax3.contourf(thompson_date_list, z, tom_relha, cmap='RdBu_r', extend='both')
    ax3.set_title('Thompson Relative Humidity Anomaly (%)')
    ax3.set_xlim([datetime(2018, 8, 21, 0, 0),datetime(2018, 8, 28, 12, 0)])
    plt.colorbar(cf, ax=ax3)

    fig.tight_layout()
    plt.show()



In [12]:
fig = plt.figure()
ax1 = fig.add_subplot(3,1,1)
ax2 = fig.add_subplot(3,1,2)
ax3 = fig.add_subplot(3,1,3)

cf = ax1.contourf(palau.sounding_date[79::], z, pal_relh[:, 79::], np.arange(-30, 30), cmap='RdBu_r', extend='both')
ax1.set_title('Palau Meridional wind (knots)')
plt.colorbar(cf, ax=ax1)

cf = ax2.contourf(yap.sounding_date[39::], z, yap_relh[:, 39::], np.arange(-30, 30), cmap='RdBu_r', extend='both')
ax2.set_title('Yap Meridional wind (knots)')
plt.colorbar(cf, ax=ax2)

cf = ax3.contourf(thompson_date_list, z, tom_relh, np.arange(-30, 30), cmap='RdBu_r', extend='both')
ax3.set_title('Thompson Meridional wind (knots)')
plt.colorbar(cf, ax=ax3)

fig.tight_layout()
plt.show()

NameError: name 'relh' is not defined

In [ ]:
plt.figure()
plt.contourf(np.arange(0,len(data_set))+1, z, relh, np.linspace(50, 100, 25), cmap='Blues')
plt.plot(np.arange(0,len(data_set))+1, z[:,-1], color='r')
plt.title('Relative humidity (%)')
plt.colorbar()
plt.show()


In [ ]:
test_list = list()
for i in range(15):
    test_list.append(i)
print(test_list)

In [16]:
yap.sounding_date

[datetime.datetime(2018, 8, 1, 0, 0),
 datetime.datetime(2018, 8, 1, 12, 0),
 datetime.datetime(2018, 8, 2, 0, 0),
 datetime.datetime(2018, 8, 2, 12, 0),
 datetime.datetime(2018, 8, 3, 0, 0),
 datetime.datetime(2018, 8, 3, 12, 0),
 datetime.datetime(2018, 8, 4, 0, 0),
 datetime.datetime(2018, 8, 4, 12, 0),
 datetime.datetime(2018, 8, 5, 0, 0),
 datetime.datetime(2018, 8, 5, 12, 0),
 datetime.datetime(2018, 8, 6, 0, 0),
 datetime.datetime(2018, 8, 6, 12, 0),
 datetime.datetime(2018, 8, 7, 0, 0),
 datetime.datetime(2018, 8, 7, 12, 0),
 datetime.datetime(2018, 8, 8, 0, 0),
 datetime.datetime(2018, 8, 8, 12, 0),
 datetime.datetime(2018, 8, 9, 0, 0),
 datetime.datetime(2018, 8, 9, 12, 0),
 datetime.datetime(2018, 8, 10, 0, 0),
 datetime.datetime(2018, 8, 10, 12, 0),
 datetime.datetime(2018, 8, 11, 0, 0),
 datetime.datetime(2018, 8, 11, 12, 0),
 datetime.datetime(2018, 8, 12, 0, 0),
 datetime.datetime(2018, 8, 12, 12, 0),
 datetime.datetime(2018, 8, 13, 0, 0),
 datetime.datetime(2018, 8, 13,